# TensorFlow : Data Parallelism multi-GPU et multi-nœuds
## Mise en pratique

*Notebook rédigé par l'équipe assistance IA de l'IDRIS, septembre 2021*

Ce document présente la méthode à adopter sur Jean Zay pour distribuer votre entraînement TensorFlow selon la méthode du ***Data Parallelism***. Il prend comme référence la [documentation TensorFlow](https://www.tensorflow.org/tutorials/distribute/multi_worker_with_keras) et illustre la [documentation IDRIS](http://www.idris.fr/jean-zay/gpu/jean-zay-gpu-tf-multi.html).

Dans l'exemple proposé, nous entraînons un réseau ResNet50 sur la base de données CIFAR10. L'apprentissage s'exécute sur plusieurs GPU et plusieurs nœuds de calcul Jean Zay.

Nous présentons :
* un [exemple d'entraînement distribué d'un modèle `tf.keras.Model`](#tfKerasModel)
* un [exemple d'entraînement distribué d'un modèle personnalisé (Custom Training Loop)](#CTL)

------------------------

### Environnement de calcul

Ce notebook est prévu pour être exécuté à partir d'une machine frontale de Jean-Zay. Le *hostname* doit être jean-zay[1-5].

In [1]:
!hostname

jean-zay4


Un module TensorFlow doit avoir été chargé pour le bon fonctionnement de ce Notebook. Par exemple, le module `tensorflow-gpu/py3/2.6.0` :

In [2]:
!module list

Currently Loaded Modulefiles:
 1) gcc/8.3.1   3) nccl/2.8.3-1-cuda     5) openmpi/4.0.5-cuda        
 2) cuda/11.2   4) cudnn/8.1.1.33-cuda   6) tensorflow-gpu/py3/2.6.0  
>

------------------------------------

### Exemple d'entraînement distribué d'un modèle de type `tf.keras.Model` <a class="anchor" id="tfKerasModel"></a>

#### Rédaction du script Python pour l'apprentissage distribué 

Dans cette section, nous rédigeons le script Python d'entraînement dans le fichier 'resnet50_distributed_keras.py'.

In [3]:
%%writefile resnet50_distributed_keras.py 
#!/usr/bin/env python
# coding: utf-8

import tensorflow as tf
import time
import os


#--- create the distribution strategy before calling any other tensorflow op
cluster_resolver = tf.distribute.cluster_resolver.SlurmClusterResolver(port_base=12345)
implementation = tf.distribute.experimental.CommunicationImplementation.NCCL
communication_options = tf.distribute.experimental.CommunicationOptions(implementation=implementation)
strategy = tf.distribute.MultiWorkerMirroredStrategy(cluster_resolver = cluster_resolver,
                                                     communication_options=communication_options)

# get task id from cluster resolver
task_info = cluster_resolver.get_task_info()
task_id = task_info[1]
#---


#--- get total number of GPUs
n_workers = int(os.environ['SLURM_NTASKS'])                    # get number of workers
devices = tf.config.experimental.list_physical_devices('GPU')  # get list of devices visible per worker
n_gpus_per_worker = len(devices)                               # get number of devices per worker
n_gpus = n_workers * n_gpus_per_worker                         # get total number of GPUs
#---


#--- define batch size and number of epochs
n_epochs = 10
batch_size_per_gpu = 32
global_batch_size= batch_size_per_gpu * n_gpus
#---


#--- load and preprocess CIFAR10 dataset from DSDIR disk space
data_dir = os.environ['DSDIR']+'/CIFAR-10-images/train/'
train_dataset = tf.keras.preprocessing.image_dataset_from_directory(
  data_dir,
  seed=123,
  image_size=(128, 128),
  batch_size=global_batch_size)
#---
   

#--- open a strategy scope to build and compile the model
with strategy.scope():
    
    # build resnet50 model
    model = tf.keras.applications.resnet_v2.ResNet50V2(include_top=True, weights=None,
                                                       input_shape=(128, 128, 3), classes=10)

    # define optimizer 
    # NB: with SGD optimizer, the learning rate must be adjusted according to global batch size
    optimizer = tf.keras.optimizers.SGD(0.01*float(n_gpus)) 

    # compile model 
    model.compile(loss='sparse_categorical_crossentropy',
                  optimizer=optimizer, metrics=['accuracy'])
#---


#--- train model and get duration

# deactivate fit verbosity on slave workers
verbosity = 2 if task_id == 0 else 0
    
start_time = time.time()
model.fit(train_dataset, epochs=n_epochs, verbose=verbosity)
duration = time.time() - start_time

if task_id == 0: # print only on master task 
    print(f'>>> Trained in {duration}s on {n_gpus} GPUs (global batch size = {global_batch_size}, nb epochs = {n_epochs})')
#---

Overwriting resnet50_distributed_keras.py


**Remarque** : la base de données CIFAR10 est disponible sur Jean Zay dans le DSDIR. Le DSDIR, comme le SCRATCH, est un espace disque GPFS dont la bande passante est d'environ 300 Go/s en écriture et en lecture. Ils sont à privilégier pour les codes ayant une utilisation intense d'opérations entrées/sorties. Le SCRATCH est dédié à vos bases privées, le DSDIR comprend des bases publiques accessibles à l'ensemble des utilisateurs de Jean Zay.

#### Lancement d'une exécution sur 1 GPU

* Écriture du script batch de soumission

**Rappel** :  si votre unique projet dispose d'heures CPU et GPU, ou encore si votre login est rattaché à plusieurs projets, vous devez impérativement préciser l'attribution sur laquelle doit être décomptée les heures consommées par vos calculs, en ajoutant l'option `--account=my_project@gpu` comme indiqué dans la [documentation IDRIS](http://www.idris.fr/jean-zay/cpu/jean-zay-cpu-doc_account.html).


In [4]:
%%writefile batch_keras_1gpu.slurm
#!/bin/bash
#SBATCH --job-name=tf_distributed_keras_1gpu
#SBATCH --output=tf_distributed_keras_1gpu.out 
#SBATCH --error=tf_distributed_keras_1gpu.err
#SBATCH --nodes=1 #---------------------------------------- 1 node
#SBATCH --ntasks=1 #--------------------------------------- 1 task / 1 worker
#SBATCH --gres=gpu:1 #------------------------------------- 1 gpu per node
#SBATCH --cpus-per-task=10
#SBATCH --hint=nomultithread 
#SBATCH --time=00:20:00
#SBATCH --qos=qos_gpu-dev
##SBATCH --account=XXX@gpu

## load TensorFlow module
module purge
module load tensorflow-gpu/py3/2.6.0

## deactivate http proxy variable so TensorFlow doesn't try to connect
set -x
unset http_proxy HTTP_PROXY https_proxy HTTPS_PROXY

## run script in parallel 
srun python3 -u resnet50_distributed_keras.py
date

Overwriting batch_keras_1gpu.slurm


* Soumission du script batch 

In [5]:
%%bash
# submit job
sbatch batch_keras_1gpu.slurm

Submitted batch job 1176999


#### Lancement d'une exécution sur 2 GPU (mono-noeud)

* Écriture du script batch de soumission

In [6]:
%%writefile batch_keras_2gpu.slurm
#!/bin/bash
#SBATCH --job-name=tf_distributed_keras_2gpu
#SBATCH --output=tf_distributed_keras_2gpu.out 
#SBATCH --error=tf_distributed_keras_2gpu.err
#SBATCH --nodes=1 #---------------------------------------- 1 node
#SBATCH --ntasks=2 #--------------------------------------- 2 tasks / 2 workers
#SBATCH --gres=gpu:2 #------------------------------------- 2 gpus per node
#SBATCH --cpus-per-task=10
#SBATCH --hint=nomultithread 
#SBATCH --time=00:20:00
#SBATCH --qos=qos_gpu-dev
##SBATCH --account=XXX@gpu

## load TensorFlow module
module purge
module load tensorflow-gpu/py3/2.6.0

## deactivate http proxy variable so TensorFlow doesn't try to connect
set -x
unset http_proxy HTTP_PROXY https_proxy HTTPS_PROXY

## run script in parallel 
srun python3 -u resnet50_distributed_keras.py 
date

Overwriting batch_keras_2gpu.slurm


* Soumission du script batch 

In [7]:
%%bash
# submit job
sbatch batch_keras_2gpu.slurm

Submitted batch job 1177003


#### Lancement d'une exécution sur 4 GPU (mono-noeud)

* Écriture du script batch de soumission

In [8]:
%%writefile batch_keras_4gpu.slurm
#!/bin/bash
#SBATCH --job-name=tf_distributed_keras_4gpu
#SBATCH --output=tf_distributed_keras_4gpu.out 
#SBATCH --error=tf_distributed_keras_4gpu.err
#SBATCH --nodes=1 #---------------------------------------- 1 node
#SBATCH --ntasks=4 #--------------------------------------- 4 tasks / 4 workers
#SBATCH --gres=gpu:4 #------------------------------------- 4 gpus per node
#SBATCH --cpus-per-task=10
#SBATCH --hint=nomultithread 
#SBATCH --time=00:20:00
#SBATCH --qos=qos_gpu-dev
##SBATCH --account=XXX@gpu

## load TensorFlow module
module purge
module load tensorflow-gpu/py3/2.6.0

## deactivate http proxy variable so TensorFlow doesn't try to connect
set -x
unset http_proxy HTTP_PROXY https_proxy HTTPS_PROXY

## run script in parallel 
srun python3 -u resnet50_distributed_keras.py 
date

Overwriting batch_keras_4gpu.slurm


* Soumission du script batch 

In [9]:
%%bash
# submit job
sbatch batch_keras_4gpu.slurm

Submitted batch job 1177051


#### Lancement d'une exécution sur 8 GPU (multi-nœuds)

* Écriture du script batch de soumission

In [10]:
%%writefile batch_keras_8gpu.slurm
#!/bin/bash
#SBATCH --job-name=tf_distributed_keras_8gpu
#SBATCH --output=tf_distributed_keras_8gpu.out 
#SBATCH --error=tf_distributed_keras_8gpu.err
#SBATCH --nodes=2 #---------------------------------------- 2 nodes
#SBATCH --ntasks=8 #--------------------------------------- 8 tasks / 8 workers
#SBATCH --gres=gpu:4 #------------------------------------- 4 gpus per node
#SBATCH --cpus-per-task=10
#SBATCH --hint=nomultithread 
#SBATCH --time=00:20:00
#SBATCH --qos=qos_gpu-dev
##SBATCH --account=XXX@gpu

## load TensorFlow module
module purge
module load tensorflow-gpu/py3/2.6.0

## deactivate http proxy variable so TensorFlow doesn't try to connect
set -x
unset http_proxy HTTP_PROXY https_proxy HTTPS_PROXY

## run script in parallel 
srun python3 -u resnet50_distributed_keras.py 
date

Overwriting batch_keras_8gpu.slurm


* Soumission du script batch 

In [11]:
%%bash
# submit job
sbatch batch_keras_8gpu.slurm

Submitted batch job 1177055


sbatch: IDRIS: setting exclusive mode for the job.


#### Affichage des résultats

On vérifie que les exécutions sont terminées en surveillant la file d'attente Slurm :

In [12]:
# watch Slurm queue line until jobs are done
# the longest run (on 1 GPU) should take less than 15 minutes
import idr_pytools
idr_pytools.display_slurm_queue()

             JOBID PARTITION     NAME     USER ST       TIME  NODES NODELIST(REASON) 
           1176999   gpu_p13 tf_distr    login CG      14:31      1 r13i3n0 

 Done!


* Durées d'entraînement :

In [13]:
%%bash
grep Trained tf_distributed_keras*

tf_distributed_keras_1gpu.out:>>> Trained in 814.4533381462097s on 1 GPUs (global batch size = 32, nb epochs = 10)
tf_distributed_keras_2gpu.out:>>> Trained in 467.11539793014526s on 2 GPUs (global batch size = 64, nb epochs = 10)
tf_distributed_keras_4gpu.out:>>> Trained in 250.4078540802002s on 4 GPUs (global batch size = 128, nb epochs = 10)
tf_distributed_keras_8gpu.out:>>> Trained in 160.8756799697876s on 8 GPUs (global batch size = 256, nb epochs = 10)


* Détails des logs :

In [14]:
%cat tf_distributed_keras_1gpu.out

Found 50000 files belonging to 10 classes.
Epoch 1/10
1563/1563 - 103s - loss: 1.6935 - accuracy: 0.3773
Epoch 2/10
1563/1563 - 77s - loss: 1.3140 - accuracy: 0.5233
Epoch 3/10
1563/1563 - 78s - loss: 1.0966 - accuracy: 0.6099
Epoch 4/10
1563/1563 - 79s - loss: 0.9261 - accuracy: 0.6738
Epoch 5/10
1563/1563 - 78s - loss: 0.7730 - accuracy: 0.7275
Epoch 6/10
1563/1563 - 79s - loss: 0.6273 - accuracy: 0.7800
Epoch 7/10
1563/1563 - 79s - loss: 0.5056 - accuracy: 0.8214
Epoch 8/10
1563/1563 - 79s - loss: 0.3972 - accuracy: 0.8616
Epoch 9/10
1563/1563 - 78s - loss: 0.2939 - accuracy: 0.8976
Epoch 10/10
1563/1563 - 77s - loss: 0.2393 - accuracy: 0.9158
>>> Trained in 814.4533381462097s on 1 GPUs (global batch size = 32, nb epochs = 10)
Fri Sep 24 15:16:57 CEST 2021


In [15]:
%cat tf_distributed_keras_2gpu.out

Found 50000 files belonging to 10 classes.
Found 50000 files belonging to 10 classes.
Epoch 1/10
782/782 - 65s - loss: 1.7046 - accuracy: 0.3690
Epoch 2/10
782/782 - 44s - loss: 1.3417 - accuracy: 0.5114
Epoch 3/10
782/782 - 44s - loss: 1.1235 - accuracy: 0.5974
Epoch 4/10
782/782 - 44s - loss: 0.9520 - accuracy: 0.6618
Epoch 5/10
782/782 - 44s - loss: 0.7916 - accuracy: 0.7241
Epoch 6/10
782/782 - 44s - loss: 0.6500 - accuracy: 0.7716
Epoch 7/10
782/782 - 44s - loss: 0.5176 - accuracy: 0.8181
Epoch 8/10
782/782 - 44s - loss: 0.3953 - accuracy: 0.8606
Epoch 9/10
782/782 - 44s - loss: 0.3058 - accuracy: 0.8926
Epoch 10/10
782/782 - 44s - loss: 0.2277 - accuracy: 0.9201
>>> Trained in 467.11539793014526s on 2 GPUs (global batch size = 64, nb epochs = 10)
Fri Sep 24 15:11:12 CEST 2021


In [16]:
%cat tf_distributed_keras_4gpu.out

Found 50000 files belonging to 10 classes.
Found 50000 files belonging to 10 classes.
Found 50000 files belonging to 10 classes.
Found 50000 files belonging to 10 classes.
Epoch 1/10
391/391 - 43s - loss: 1.7555 - accuracy: 0.3534
Epoch 2/10
391/391 - 22s - loss: 1.3550 - accuracy: 0.5057
Epoch 3/10
391/391 - 22s - loss: 1.1345 - accuracy: 0.5956
Epoch 4/10
391/391 - 22s - loss: 0.9566 - accuracy: 0.6604
Epoch 5/10
391/391 - 22s - loss: 0.8070 - accuracy: 0.7135
Epoch 6/10
391/391 - 22s - loss: 0.6779 - accuracy: 0.7597
Epoch 7/10
391/391 - 22s - loss: 0.5393 - accuracy: 0.8089
Epoch 8/10
391/391 - 22s - loss: 0.4194 - accuracy: 0.8529
Epoch 9/10
391/391 - 22s - loss: 0.3215 - accuracy: 0.8868
Epoch 10/10
391/391 - 22s - loss: 0.2559 - accuracy: 0.9090
>>> Trained in 250.4078540802002s on 4 GPUs (global batch size = 128, nb epochs = 10)
Fri Sep 24 15:07:35 CEST 2021


In [17]:
%cat tf_distributed_keras_8gpu.out

Found 50000 files belonging to 10 classes.
Found 50000 files belonging to 10 classes.
Found 50000 files belonging to 10 classes.
Found 50000 files belonging to 10 classes.
Found 50000 files belonging to 10 classes.
Found 50000 files belonging to 10 classes.
Found 50000 files belonging to 10 classes.
Found 50000 files belonging to 10 classes.
Epoch 1/10
196/196 - 33s - loss: 2.1477 - accuracy: 0.2989
Epoch 2/10
196/196 - 14s - loss: 1.5183 - accuracy: 0.4632
Epoch 3/10
196/196 - 14s - loss: 1.2741 - accuracy: 0.5439
Epoch 4/10
196/196 - 14s - loss: 1.0986 - accuracy: 0.6113
Epoch 5/10
196/196 - 14s - loss: 0.9258 - accuracy: 0.6702
Epoch 6/10
196/196 - 14s - loss: 0.7913 - accuracy: 0.7203
Epoch 7/10
196/196 - 14s - loss: 0.6520 - accuracy: 0.7692
Epoch 8/10
196/196 - 14s - loss: 0.5269 - accuracy: 0.8132
Epoch 9/10
196/196 - 14s - loss: 0.4202 - accuracy: 0.8505
Epoch 10/10
196/196 - 14s - loss: 0.3053 - accuracy: 0.8939
>>> Trained in 160.8756799697876s on 8 GPUs (global batch size = 

### Exemple d'entraînement distribué d'un modèle personnalisé (Custom Training Loop) <a class="anchor" id="CTL"></a>

#### Rédaction du script Python pour l'apprentissage distribué 

Dans cette section, nous rédigeons le script Python d'entraînement dans le fichier 'resnet50_distributed_ctl.py'.

In [18]:
%%writefile resnet50_distributed_ctl.py 
#!/usr/bin/env python
# coding: utf-8

import tensorflow as tf
import time
import os


#--- create the distribution strategy before calling any other tensorflow op
cluster_resolver = tf.distribute.cluster_resolver.SlurmClusterResolver(port_base=12345)
implementation = tf.distribute.experimental.CommunicationImplementation.NCCL
communication_options = tf.distribute.experimental.CommunicationOptions(implementation=implementation)
strategy = tf.distribute.MultiWorkerMirroredStrategy(cluster_resolver = cluster_resolver,
                                                     communication_options=communication_options)

# get task id from cluster resolver
task_info = cluster_resolver.get_task_info()
task_id = task_info[1]
#---


#--- get total number of GPUs
n_workers = int(os.environ['SLURM_NTASKS'])                    # get number of workers
devices = tf.config.experimental.list_physical_devices('GPU')  # get list of devices visible per worker
n_gpus_per_worker = len(devices)                               # get number of devices per worker
n_gpus = n_workers * n_gpus_per_worker                         # get total number of GPUs
#---


#--- define batch size and number of epochs
n_epochs = 10
batch_size_per_gpu = 32
global_batch_size= batch_size_per_gpu * n_gpus

#---


#--- load and preprocess CIFAR10 dataset from DSDIR disk space
data_dir = os.environ['DSDIR']+'/CIFAR-10-images/train/'
train_dataset = tf.keras.preprocessing.image_dataset_from_directory(
  data_dir,
  seed=123,
  image_size=(128, 128),
  batch_size=global_batch_size)
#---


#--- define num_steps_per_epoch
num_steps_per_epoch = len(train_dataset)
#---


#--- open a strategy scope to build and compile the multi_worker_model
with strategy.scope():
    
    # build resnet50 multi_worker_model
    multi_worker_model = tf.keras.applications.resnet_v2.ResNet50V2(include_top=True, weights=None,
                                                       input_shape=(128, 128, 3), classes=10)
    
    # data sharding
    multi_worker_dataset = strategy.experimental_distribute_dataset(train_dataset)

    # define optimizer 
    # NB: with SGD optimizer, the learning rate must be adjusted according to global batch size
    optimizer = tf.keras.optimizers.SGD(0.01*float(n_gpus)) 

    # define accuracy function 
    train_accuracy = tf.keras.metrics.SparseCategoricalAccuracy(name='train_accuracy')
#---


#--- define the training step
@tf.function
def train_step(iterator): # ---------------------------------------------------- training step 
 
    def step_fn(inputs): # ------------------------------------------------------- per-GPU step
 
        x, y = inputs
        with tf.GradientTape() as tape:
 
            # compute predictions
            predictions = multi_worker_model(x, training=True)
 
            # compute the loss for each batch between the labels and predictions
            # IMPORTANT: set reduction to NONE so we can do the reduction afterwards and divide by global batch size
            reduction = tf.keras.losses.Reduction.NONE
            losses_per_batch = tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True,
                                                                       reduction=reduction)(y, predictions)
 
            # sum losses per batch and divide by global batch size
            loss = tf.nn.compute_average_loss(losses_per_batch, global_batch_size=global_batch_size)
 
        # compute and apply gradients
        grads = tape.gradient(loss, multi_worker_model.trainable_variables)
        optimizer.apply_gradients(zip(grads, multi_worker_model.trainable_variables))
 
        # compute accuracy
        train_accuracy.update_state(y, predictions)
 
        return loss
 
    # `strategy.run()` invokes step_fn on each GPU
    loss_per_gpu = strategy.run(step_fn, args=(next(iterator),))
 
    # `strategy.reduce()` reduces given value across GPUs and return result on current device  
    return strategy.reduce(tf.distribute.ReduceOp.SUM, loss_per_gpu, axis=None)
#---


#--- train multi_worker_model and get duration
# intialize training
start_time = time.time()
epoch = 0
step_in_epoch = 0

# run training
while epoch < n_epochs:
    if task_id==0:
        print(f'Epoch {epoch+1}/{n_epochs}')
 
    # intialize step
    iterator = iter(multi_worker_dataset)
    total_loss = 0.0
    num_batches = 0
    start_time_epoch = time.time()

    # run steps
    while step_in_epoch < num_steps_per_epoch:
        total_loss += train_step(iterator) # ------- call training step function
        num_batches += 1
        step_in_epoch +=1

    train_loss = total_loss / num_batches

    # display information per epoch
    duration_epoch = time.time() - start_time_epoch
    acc=train_accuracy.result()
    if task_id==0:
        print(f'{step_in_epoch}/{num_steps_per_epoch} - {duration_epoch}s - loss: {train_loss} - accuracy: {acc}')

    # reset for next epoch
    epoch +=1
    step_in_epoch = 0
    train_accuracy.reset_states()

duration = time.time() - start_time
if task_id==0:
    print(f'>>> Trained in {duration}s on {n_gpus} GPUs (global batch size = {global_batch_size}, nb epochs = {n_epochs})')
#---

Overwriting resnet50_distributed_ctl.py


**Remarque** : la base de données CIFAR10 est disponible sur Jean Zay dans le DSDIR. Le DSDIR, comme le SCRATCH, est un espace disque GPFS dont la bande passante est d'environ 300 Go/s en écriture et en lecture. Ils sont à privilégier pour les codes ayant une utilisation intense d'opérations entrées/sorties. Le SCRATCH est dédié à vos bases privées, le DSDIR comprend des bases publiques accessibles à l'ensemble des utilisateurs de Jean Zay.

#### Lancement d'une exécution sur 1 GPU

* Écriture du script batch de soumission

**Rappel** :  si votre unique projet dispose d'heures CPU et GPU, ou encore si votre login est rattaché à plusieurs projets, vous devez impérativement préciser l'attribution sur laquelle doit être décomptée les heures consommées par vos calculs, en ajoutant l'option `--account=my_project@gpu` comme indiqué dans la [documentation IDRIS](http://www.idris.fr/jean-zay/cpu/jean-zay-cpu-doc_account.html).


In [19]:
%%writefile batch_ctl_1gpu.slurm
#!/bin/bash
#SBATCH --job-name=tf_distributed_ctl_1gpu
#SBATCH --output=tf_distributed_ctl_1gpu.out 
#SBATCH --error=tf_distributed_ctl_1gpu.err
#SBATCH --nodes=1 #---------------------------------------- 1 node
#SBATCH --ntasks=1 #--------------------------------------- 1 task / 1 worker
#SBATCH --gres=gpu:1 #------------------------------------- 1 gpu per node
#SBATCH --cpus-per-task=10
#SBATCH --hint=nomultithread 
#SBATCH --time=00:20:00
#SBATCH --qos=qos_gpu-dev
##SBATCH --account=XXX@gpu

## load TensorFlow module
module purge
module load tensorflow-gpu/py3/2.6.0

## deactivate http proxy variable so TensorFlow doesn't try to connect
set -x
unset http_proxy HTTP_PROXY https_proxy HTTPS_PROXY

## run script in parallel 
srun python3 -u resnet50_distributed_ctl.py
date

Overwriting batch_ctl_1gpu.slurm


* Soumission du script batch 

In [20]:
%%bash
# submit job
sbatch batch_ctl_1gpu.slurm

Submitted batch job 1177928


#### Lancement d'une exécution sur 2 GPU (mono-noeud)

* Écriture du script batch de soumission

In [21]:
%%writefile batch_ctl_2gpu.slurm
#!/bin/bash
#SBATCH --job-name=tf_distributed_ctl_2gpu
#SBATCH --output=tf_distributed_ctl_2gpu.out 
#SBATCH --error=tf_distributed_ctl_2gpu.err
#SBATCH --nodes=1 #---------------------------------------- 1 node
#SBATCH --ntasks=2 #--------------------------------------- 2 tasks / 2 workers
#SBATCH --gres=gpu:2 #------------------------------------- 2 gpus per node
#SBATCH --cpus-per-task=10
#SBATCH --hint=nomultithread 
#SBATCH --time=00:20:00
#SBATCH --qos=qos_gpu-dev
##SBATCH --account=XXX@gpu

## load TensorFlow module
module purge
module load tensorflow-gpu/py3/2.6.0

## deactivate http proxy variable so TensorFlow doesn't try to connect
set -x
unset http_proxy HTTP_PROXY https_proxy HTTPS_PROXY

## run script in parallel 
srun python3 -u resnet50_distributed_ctl.py
date

Overwriting batch_ctl_2gpu.slurm


* Soumission du script batch 

In [22]:
%%bash
# submit job
sbatch batch_ctl_2gpu.slurm

Submitted batch job 1177929


#### Lancement d'une exécution sur 4 GPU (mono-noeud)

* Écriture du script batch de soumission

In [23]:
%%writefile batch_ctl_4gpu.slurm
#!/bin/bash
#SBATCH --job-name=tf_distributed_ctl_4gpu
#SBATCH --output=tf_distributed_ctl_4gpu.out 
#SBATCH --error=tf_distributed_ctl_4gpu.err
#SBATCH --nodes=1 #---------------------------------------- 1 node
#SBATCH --ntasks=4 #--------------------------------------- 4 tasks / 4 workers
#SBATCH --gres=gpu:4 #------------------------------------- 4 gpus per node
#SBATCH --cpus-per-task=10
#SBATCH --hint=nomultithread 
#SBATCH --time=00:20:00
#SBATCH --qos=qos_gpu-dev
##SBATCH --account=XXX@gpu

## load TensorFlow module
module purge
module load tensorflow-gpu/py3/2.6.0

## deactivate http proxy variable so TensorFlow doesn't try to connect
set -x
unset http_proxy HTTP_PROXY https_proxy HTTPS_PROXY

## run script in parallel 
srun python3 -u resnet50_distributed_ctl.py
date

Overwriting batch_ctl_4gpu.slurm


* Soumission du script batch 

In [24]:
%%bash
# submit job
sbatch batch_ctl_4gpu.slurm

Submitted batch job 1177930


#### Lancement d'une exécution sur 8 GPU (multi-noeuds)

* Écriture du script batch de soumission

In [25]:
%%writefile batch_ctl_8gpu.slurm
#!/bin/bash
#SBATCH --job-name=tf_distributed_ctl_8gpu
#SBATCH --output=tf_distributed_ctl_8gpu.out 
#SBATCH --error=tf_distributed_ctl_8gpu.err
#SBATCH --nodes=2 #---------------------------------------- 2 nodes
#SBATCH --ntasks=8 #--------------------------------------- 8 tasks / 8 workers
#SBATCH --gres=gpu:4 #------------------------------------- 4 gpus per node
#SBATCH --cpus-per-task=10
#SBATCH --hint=nomultithread 
#SBATCH --time=00:20:00
#SBATCH --qos=qos_gpu-dev
##SBATCH --account=XXX@gpu

## load TensorFlow module
module purge
module load tensorflow-gpu/py3/2.6.0

## deactivate http proxy variable so TensorFlow doesn't try to connect
set -x
unset http_proxy HTTP_PROXY https_proxy HTTPS_PROXY

## run script in parallel 
srun python3 -u resnet50_distributed_ctl.py
date

Overwriting batch_ctl_8gpu.slurm


* Soumission du script batch 

In [26]:
%%bash
# submit job
sbatch batch_ctl_8gpu.slurm

Submitted batch job 1177931


sbatch: IDRIS: setting exclusive mode for the job.


#### Affichage des résultats

On vérifie que les exécutions sont terminées en surveillant la file d'attente Slurm :

In [27]:
# watch Slurm queue line until jobs are done
# the longest run (on 1 GPU) should take less than 15 minutes
import idr_pytools
idr_pytools.display_slurm_queue()

             JOBID PARTITION     NAME     USER ST       TIME  NODES NODELIST(REASON) 
           1177928   gpu_p13 tf_distr    login  R      13:55      1 r11i0n2 

 Done!


* Durées des entraînements :

In [28]:
%%bash
grep Trained tf_distributed_ctl*

tf_distributed_ctl_1gpu.out:>>> Trained in 788.883195400238s on 1 GPUs (global batch size = 32, nb epochs = 10)
tf_distributed_ctl_2gpu.out:>>> Trained in 455.658864736557s on 2 GPUs (global batch size = 64, nb epochs = 10)
tf_distributed_ctl_4gpu.out:>>> Trained in 240.36389923095703s on 4 GPUs (global batch size = 128, nb epochs = 10)
tf_distributed_ctl_8gpu.out:>>> Trained in 155.73444652557373s on 8 GPUs (global batch size = 256, nb epochs = 10)


* Détails des logs :

In [29]:
%cat tf_distributed_ctl_1gpu.out

Found 50000 files belonging to 10 classes.
Epoch 1/10
1563/1563 - 96.2693178653717s - loss: 1.677822470664978 - accuracy: 0.3838199973106384
Epoch 2/10
1563/1563 - 76.98866939544678s - loss: 1.2866010665893555 - accuracy: 0.5364999771118164
Epoch 3/10
1563/1563 - 76.92621850967407s - loss: 1.0735931396484375 - accuracy: 0.6164199709892273
Epoch 4/10
1563/1563 - 76.87359976768494s - loss: 0.9074981212615967 - accuracy: 0.6793000102043152
Epoch 5/10
1563/1563 - 76.83586931228638s - loss: 0.7585970163345337 - accuracy: 0.7323799729347229
Epoch 6/10
1563/1563 - 76.92030835151672s - loss: 0.6183837056159973 - accuracy: 0.7826200127601624
Epoch 7/10
1563/1563 - 76.83458137512207s - loss: 0.48463910818099976 - accuracy: 0.828000009059906
Epoch 8/10
1563/1563 - 76.90729641914368s - loss: 0.37467119097709656 - accuracy: 0.8688399791717529
Epoch 9/10
1563/1563 - 76.84513473510742s - loss: 0.2894079089164734 - accuracy: 0.8984000086784363
Epoch 10/10
1563/1563 - 76.85867810249329s - loss: 0.22137

In [30]:
%cat tf_distributed_ctl_2gpu.out

Found 50000 files belonging to 10 classes.
Found 50000 files belonging to 10 classes.
Epoch 1/10
782/782 - 62.59337401390076s - loss: 1.7095335721969604 - accuracy: 0.3655399978160858
Epoch 2/10
782/782 - 43.650728702545166s - loss: 1.326806902885437 - accuracy: 0.5176399946212769
Epoch 3/10
782/782 - 43.64861011505127s - loss: 1.126267433166504 - accuracy: 0.5965399742126465
Epoch 4/10
782/782 - 43.65208411216736s - loss: 0.9559903740882874 - accuracy: 0.6614000201225281
Epoch 5/10
782/782 - 43.60719108581543s - loss: 0.8060988783836365 - accuracy: 0.7152400016784668
Epoch 6/10
782/782 - 43.642653465270996s - loss: 0.6634347438812256 - accuracy: 0.7659800052642822
Epoch 7/10
782/782 - 43.5941162109375s - loss: 0.5303032398223877 - accuracy: 0.8144199848175049
Epoch 8/10
782/782 - 43.580815076828s - loss: 0.4127270579338074 - accuracy: 0.8534600138664246
Epoch 9/10
782/782 - 43.587456941604614s - loss: 0.31168341636657715 - accuracy: 0.8899000287055969
Epoch 10/10
782/782 - 43.56369709

In [31]:
%cat tf_distributed_ctl_4gpu.out

Found 50000 files belonging to 10 classes.
Found 50000 files belonging to 10 classes.
Found 50000 files belonging to 10 classes.
Found 50000 files belonging to 10 classes.
Epoch 1/10
391/391 - 39.55311679840088s - loss: 1.7514476776123047 - accuracy: 0.3552800118923187
Epoch 2/10
391/391 - 22.320881128311157s - loss: 1.3784465789794922 - accuracy: 0.4967400133609772
Epoch 3/10
391/391 - 22.260685682296753s - loss: 1.1774667501449585 - accuracy: 0.5740200281143188
Epoch 4/10
391/391 - 22.256728887557983s - loss: 0.9981435537338257 - accuracy: 0.6444200277328491
Epoch 5/10
391/391 - 22.265665769577026s - loss: 0.8433294892311096 - accuracy: 0.7021200060844421
Epoch 6/10
391/391 - 22.22460627555847s - loss: 0.6997244954109192 - accuracy: 0.7522199749946594
Epoch 7/10
391/391 - 22.234546899795532s - loss: 0.5648218989372253 - accuracy: 0.8004800081253052
Epoch 8/10
391/391 - 22.224921464920044s - loss: 0.44459202885627747 - accuracy: 0.8451399803161621
Epoch 9/10
391/391 - 22.2603130340576

In [32]:
%cat tf_distributed_ctl_8gpu.out

Found 50000 files belonging to 10 classes.
Found 50000 files belonging to 10 classes.
Found 50000 files belonging to 10 classes.
Found 50000 files belonging to 10 classes.
Found 50000 files belonging to 10 classes.
Found 50000 files belonging to 10 classes.
Found 50000 files belonging to 10 classes.
Found 50000 files belonging to 10 classes.
Epoch 1/10
196/196 - 31.589051485061646s - loss: 2.1382858753204346 - accuracy: 0.3003999888896942
Epoch 2/10
196/196 - 13.732277870178223s - loss: 1.5197434425354004 - accuracy: 0.4582799971103668
Epoch 3/10
196/196 - 13.6619234085083s - loss: 1.26650869846344 - accuracy: 0.546180009841919
Epoch 4/10
196/196 - 13.74026346206665s - loss: 1.072035789489746 - accuracy: 0.6134799718856812
Epoch 5/10
196/196 - 13.725396394729614s - loss: 0.9130420088768005 - accuracy: 0.6747199892997742
Epoch 6/10
196/196 - 13.702377080917358s - loss: 0.775505781173706 - accuracy: 0.7234600186347961
Epoch 7/10
196/196 - 13.723385572433472s - loss: 0.6478542685508728 - 